# Import Libraries

In [45]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library


In [46]:
# send the GET request
data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(data, 'html.parser')

# create three lists to store table data
postalCodeList = []
boroughList = []
neighborhoodList = []

In [ ]:
# append the data into the respective lists
for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        postalCodeList.append(cells[0].text)
        boroughList.append(cells[1].text)
        neighborhoodList.append(cells[2].text.rstrip('\n')) # avoid new lines in neighborhood cell


## Remove 'unnassigned' Boroughs

In [3]:
#Remove Boroughs that are 'Not assigned'
canada_df = canada_df[canada_df['Borough'] != 'Not assigned']
canada_df.head()
canada_df.shape

(210, 3)

## Overview

In [4]:
canada_df.shape

(210, 3)

In [5]:
canada_df.reset_index(drop=True, inplace=True)

In [6]:
print('There are %d unique Postal Codes in the table' % canada_df.Postcode.nunique())
print('There are %d unique Boroughs in the table' % canada_df.Borough.nunique())
print('There are %d unique Neighbourhoods in the table' % canada_df.Neighborhood.nunique())

There are 103 unique Postal Codes in the table
There are 11 unique Boroughs in the table
There are 208 unique Neighbourhoods in the table


## Group Neighbourhoods by Postal code

In [7]:
part_01 = pd.DataFrame(canada_df.groupby(
    ['Postcode', 'Borough'])['Neighborhood'].apply(
    lambda x: ', '.join(x))).reset_index()

In [8]:
part_01.head()

Postcode      Borough                            Neighborhood
0      M1B  Scarborough                          Rouge, Malvern
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2      M1E  Scarborough       Guildwood, Morningside, West Hill
3      M1G  Scarborough                                  Woburn
4      M1H  Scarborough                               Cedarbrae

In [9]:
part_01.tail()

Postcode    Borough                                       Neighborhood
98       M9N       York                                             Weston
99       M9P  Etobicoke                                          Westmount
100      M9R  Etobicoke  Kingsview Village, Martin Grove Gardens, Richv...
101      M9V  Etobicoke  Albion Gardens, Beaumond Heights, Humbergate, ...
102      M9W  Etobicoke                                          Northwest

In [10]:
part_01.shape

(103, 3)

# Geocode the city data

In [11]:
geocoded = pd.read_csv('Geospatial_Coordinates.csv')

In [12]:
geocoded.shape

(103, 3)

In [13]:
canada_df.shape

(210, 3)

In [14]:
df = part_01.join(geocoded)

In [15]:
df.drop('Postal Code', axis=1)

Postcode           Borough  \
0        M1B       Scarborough   
1        M1C       Scarborough   
2        M1E       Scarborough   
3        M1G       Scarborough   
4        M1H       Scarborough   
5        M1J       Scarborough   
6        M1K       Scarborough   
7        M1L       Scarborough   
8        M1M       Scarborough   
9        M1N       Scarborough   
10       M1P       Scarborough   
11       M1R       Scarborough   
12       M1S       Scarborough   
13       M1T       Scarborough   
14       M1V       Scarborough   
15       M1W       Scarborough   
16       M1X       Scarborough   
17       M2H        North York   
18       M2J        North York   
19       M2K        North York   
20       M2L        North York   
21       M2M        North York   
22       M2N        North York   
23       M2P        North York   
24       M2R        North York   
25       M3A        North York   
26       M3B        North York   
27       M3C        North York   
28       M3H        North York   
29       M3J        North York   
30       M3K        North York   
31       M3L        North York   
32       M3M        North York   
33       M3N        North York   
34       M4A        North York   
35       M4B         East York   
36       M4C         East York   
37       M4E      East Toronto   
38       M4G         East York   
39       M4H         East York   
40       M4J         East York   
41       M4K      East Toronto   
42       M4L      East Toronto   
43       M4M      East Toronto   
44       M4N   Central Toronto   
45       M4P   Central Toronto   
46       M4R   Central Toronto   
47       M4S   Central Toronto   
48       M4T   Central Toronto   
49       M4V   Central Toronto   
50       M4W  Downtown Toronto   
51       M4X  Downtown Toronto   
52       M4Y  Downtown Toronto   
53       M5A  Downtown Toronto   
54       M5B  Downtown Toronto   
55       M5C  Downtown Toronto   
56       M5E  Downtown Toronto   
57       M5G  Downtown Toronto   
58       M5H  Downtown Toronto   
59       M5J  Downtown Toronto   
60       M5K  Downtown Toronto   
61       M5L  Downtown Toronto   
62       M5M        North York   
63       M5N   Central Toronto   
64       M5P   Central Toronto   
65       M5R   Central Toronto   
66       M5S  Downtown Toronto   
67       M5T  Downtown Toronto   
68       M5V  Downtown Toronto   
69       M5W  Downtown Toronto   
70       M5X  Downtown Toronto   
71       M6A        North York   
72       M6B        North York   
73       M6C              York   
74       M6E              York   
75       M6G  Downtown Toronto   
76       M6H      West Toronto   
77       M6J      West Toronto   
78       M6K      West Toronto   
79       M6L        North York   
80       M6M              York   
81       M6N              York   
82       M6P      West Toronto   
83       M6R      West Toronto   
84       M6S      West Toronto   
85       M7A  Downtown Toronto   
86       M7R       Mississauga   
87       M7Y      East Toronto   
88       M8V         Etobicoke   
89       M8W         Etobicoke   
90       M8X         Etobicoke   
91       M8Y         Etobicoke   
92       M8Z         Etobicoke   
93       M9A      Queen's Park   
94       M9B         Etobicoke   
95       M9C         Etobicoke   
96       M9L        North York   
97       M9M        North York   
98       M9N              York   
99       M9P         Etobicoke   
100      M9R         Etobicoke   
101      M9V         Etobicoke   
102      M9W         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                       Rouge, Malvern  43.806686 -79.194353  
1               Highland Creek, Rouge Hill, Port Union  43.784535 -79.160497  
2                    Guildwood, Morningside, West Hill  43.763573 -79.188711  
3                                               Woburn  43.770992 -79.216917  
4                                            Cedarbrae  43.773136 -79.23

# Implementing Folium and Foursquare 

In [16]:
address = 'Toronto'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


## Generate map of neighbourhoods

In [17]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

## Foursquare

In [18]:
CLIENT_ID = 'NAMIRBRULHHTRZ32TA4R5EIEEZYENIIYOLDYG1JJJRWUNWYE' # your Foursquare ID
CLIENT_SECRET = '3XUW3QS5WWREFXA3SLWCML0DEDH0DCMOSP4W5K4NP2PUZNIE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: NAMIRBRULHHTRZ32TA4R5EIEEZYENIIYOLDYG1JJJRWUNWYE
CLIENT_SECRET:3XUW3QS5WWREFXA3SLWCML0DEDH0DCMOSP4W5K4NP2PUZNIE


In [19]:
radius = 500
LIMIT = 100

venues = []

for lat, long, post, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Postcode'], df['Borough'], df['Neighborhood']):
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            post, 
            borough,
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

## convert the venues list into a new DataFrame

In [20]:
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['PostalCode', 'Borough', 'Neighborhood', 'BoroughLatitude', 'BoroughLongitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(2238, 9)


PostalCode      Borough                            Neighborhood  \
0        M1B  Scarborough                          Rouge, Malvern   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union   
2        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union   
3        M1E  Scarborough       Guildwood, Morningside, West Hill   
4        M1E  Scarborough       Guildwood, Morningside, West Hill   

   BoroughLatitude  BoroughLongitude                        VenueName  \
0        43.806686        -79.194353                          Wendy's   
1        43.784535        -79.160497            Royal Canadian Legion   
2        43.784535        -79.160497   Scarborough Historical Society   
3        43.763573        -79.188711  Swiss Chalet Rotisserie & Grill   
4        43.763573        -79.188711                G & G Electronics   

   VenueLatitude  VenueLongitude         VenueCategory  
0      43.807448      -79.199056  Fast Food Restaurant  
1      43.782533      -79.163085                   Bar  
2      43.788755      -79.162438        History Museum  
3      43.767697      -79.189914           Pizza Place  
4      43.765309      -79.191537     Electronics Store

## number of venues per postal code

In [21]:
venues_df.groupby(["PostalCode", "Borough", "Neighborhood"]).count()

BoroughLatitude  \
PostalCode Borough          Neighborhood                                                          
M1B        Scarborough      Rouge, Malvern                                                    1   
M1C        Scarborough      Highland Creek, Rouge Hill, Port Union                            2   
M1E        Scarborough      Guildwood, Morningside, West Hill                                 8   
M1G        Scarborough      Woburn                                                            3   
M1H        Scarborough      Cedarbrae                                                         9   
M1J        Scarborough      Scarborough Village                                               2   
M1K        Scarborough      East Birchmount Park, Ionview, Kennedy Park                       5   
M1L        Scarborough      Clairlea, Golden Mile, Oakridge                                   9   
M1M        Scarborough      Cliffcrest, Cliffside, Scarborough Village West                   4   
M1N        Scarborough      Birch Cliff, Cliffside West                                       4   
M1P        Scarborough      Dorset Park, Scarborough Town Centre, Wexford H...                7   
M1R        Scarborough      Maryvale, Wexford                                                 8   
M1S        Scarborough      Agincourt                                                         4   
M1T        Scarborough      Clarks Corners, Sullivan, Tam O'Shanter                          11   
M1V        Scarborough      Agincourt North, L'Amoreaux East, Milliken, Ste...                4   
M1W        Scarborough      L'Amoreaux West                                                  17   
M2H        North York       Hillcrest Village                                                 5   
M2J        North York       Fairview, Henry Farm, Oriole                                     62   
M2K        North York       Bayview Village                                                   4   
M2N        North York       Willowdale South                                                 35   
M2P        North York       York Mills West                                                   4   
M2R        North York       Willowdale West                                                   6   
M3A        North York       Parkwoods                                                         2   
M3B        North York       Don Mills North                                                   4   
M3C        North York       Flemingdon Park, Don Mills South                                 21   
M3H        North York       Bathurst Manor, Downsview North, Wilson Heights                  20   
M3J        North York       Northwood Park, York University                                   6   
M3K        North York       CFB Toronto, Downsview East                                       3   
M3L        North York       Downsview West                                                    5   
M3M        North York       Downsview Central                                                 3   
M3N        North York       Downsview Northwest                                               4   
M4A        North York       Victoria Village                                                  6   
M4B        East York        Woodbine Gardens, Parkview Hill                                  10   
M4C        East York        Woodbine Heights                                                  7   
M4E        East Toronto     The Beaches                                                       4   
M4G        East York        Leaside                                                          32   
M4H        East York        Thorncliffe Park                                                 18   
M4J        East York        East Toronto                                                      4   
M4K        East Toronto     The Danforth West, Riverdale                                     42   
M4L        East Toron

## Unique categories

In [22]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 271 uniques categories.


In [23]:
venues_df['VenueCategory'].unique()[:50]

array(['Fast Food Restaurant', 'Bar', 'History Museum', 'Pizza Place',
       'Electronics Store', 'Spa', 'Mexican Restaurant',
       'Rental Car Location', 'Medical Center', 'Intersection',
       'Breakfast Spot', 'Coffee Shop', 'Korean Restaurant',
       'Hakka Restaurant', 'Caribbean Restaurant', 'Thai Restaurant',
       'Athletics & Sports', 'Bank', 'Gas Station', 'Bakery', 'Lounge',
       'Fried Chicken Joint', 'Playground', 'Business Service',
       'Department Store', 'Chinese Restaurant', 'Hobby Shop',
       'Discount Store', 'Bus Line', 'Bus Station', 'Park',
       'Soccer Field', 'Motel', 'Movie Theater', 'American Restaurant',
       'Café', 'General Entertainment', 'Skating Rink', 'College Stadium',
       'Indian Restaurant', 'Vietnamese Restaurant', 'Pet Store',
       'Light Rail Station', 'Brewery', 'Sandwich Place',
       'Middle Eastern Restaurant', 'Shopping Mall', 'Auto Garage',
       'Accessories Store', 'Latin American Restaurant'], dtype=object)

## Analyze the Postal Code

### One-hot encoded, add relevant columns

In [24]:
# one hot encoding
toronto_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add postal, borough and neighborhood column back to dataframe
toronto_onehot['PostalCode'] = venues_df['PostalCode'] 
toronto_onehot['Borough'] = venues_df['Borough'] 
toronto_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move postal, borough and neighborhood column to the first column
fixed_columns = list(toronto_onehot.columns[-3:]) + list(toronto_onehot.columns[:-3])
toronto_onehot = toronto_onehot[fixed_columns]

print(toronto_onehot.shape)
toronto_onehot.head()

(2238, 274)


PostalCode      Borough                           Neighborhoods  \
0        M1B  Scarborough                          Rouge, Malvern   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union   
2        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union   
3        M1E  Scarborough       Guildwood, Morningside, West Hill   
4        M1E  Scarborough       Guildwood, Morningside, West Hill   

   Accessories Store  Airport  Airport Food Court  Airport Gate  \
0                  0        0                   0             0   
1                  0        0                   0             0   
2                  0        0                   0             0   
3                  0        0                   0             0   
4                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0         0            0                    0                 0   
1             0         0            0                    0                 0   
2             0         0            0                    0                 0   
3             0         0            0                    0                 0   
4             0         0            0                    0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0                   0            0              0          0           0   
1                   0            0              0          0           0   
2                   0            0              0          0           0   
3                   0            0              0          0           0   
4                   0            0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    1               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Board Shop  \
0           0                   0          0       0           0   
1           0                   0          0       0           0   
2           0                   0          0       0           0   
3           0                   0          0       0           0   
4           0                   0          0       0           0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0              0          0         0                     0               0   
1              0          0         0                     0               0   
2              0          0         0                     0               0   
3              0          0         0                     0               0   
4              0          0         0                     0               0   

   Brewer

### Group data by mean frequency

In [25]:
toronto_grouped = toronto_onehot.groupby(["PostalCode", "Borough", "Neighborhoods"]).mean().reset_index()

print(toronto_grouped.shape)
toronto_grouped

(99, 274)


PostalCode           Borough  \
0         M1B       Scarborough   
1         M1C       Scarborough   
2         M1E       Scarborough   
3         M1G       Scarborough   
4         M1H       Scarborough   
5         M1J       Scarborough   
6         M1K       Scarborough   
7         M1L       Scarborough   
8         M1M       Scarborough   
9         M1N       Scarborough   
10        M1P       Scarborough   
11        M1R       Scarborough   
12        M1S       Scarborough   
13        M1T       Scarborough   
14        M1V       Scarborough   
15        M1W       Scarborough   
16        M2H        North York   
17        M2J        North York   
18        M2K        North York   
19        M2N        North York   
20        M2P        North York   
21        M2R        North York   
22        M3A        North York   
23        M3B        North York   
24        M3C        North York   
25        M3H        North York   
26        M3J        North York   
27        M3K        North York   
28        M3L        North York   
29        M3M        North York   
30        M3N        North York   
31        M4A        North York   
32        M4B         East York   
33        M4C         East York   
34        M4E      East Toronto   
35        M4G         East York   
36        M4H         East York   
37        M4J         East York   
38        M4K      East Toronto   
39        M4L      East Toronto   
40        M4M      East Toronto   
41        M4N   Central Toronto   
42        M4P   Central Toronto   
43        M4R   Central Toronto   
44        M4S   Central Toronto   
45        M4T   Central Toronto   
46        M4V   Central Toronto   
47        M4W  Downtown Toronto   
48        M4X  Downtown Toronto   
49        M4Y  Downtown Toronto   
50        M5A  Downtown Toronto   
51        M5B  Downtown Toronto   
52        M5C  Downtown Toronto   
53        M5E  Downtown Toronto   
54        M5G  Downtown Toronto   
55        M5H  Downtown Toronto   
56        M5J  Downtown Toronto   
57        M5K  Downtown Toronto   
58        M5L  Downtown Toronto   
59        M5M        North York   
60        M5N   Central Toronto   
61        M5P   Central Toronto   
62        M5R   Central Toronto   
63        M5S  Downtown Toronto   
64        M5T  Downtown Toronto   
65        M5V  Downtown Toronto   
66        M5W  Downtown Toronto   
67        M5X  Downtown Toronto   
68        M6A        North York   
69        M6B        North York   
70        M6C              York   
71        M6E              York   
72        M6G  Downtown Toronto   
73        M6H      West Toronto   
74        M6J      West Toronto   
75        M6K      West Toronto   
76        M6L        North York   
77        M6M              York   
78        M6N              York   
79        M6P      West Toronto   
80        M6R      West Toronto   
81        M6S      West Toronto   
82        M7A  Downtown Toronto   
83        M7R       Mississauga   
84        M7Y      East Toronto   
85        M8V         Etobicoke   
86        M8W         Etobicoke   
87        M8X         Etobicoke   
88        M8Y         Etobicoke   
89        M8Z         Etobicoke   
90        M9B         Etobicoke   
91        M9C         Etobicoke   
92        M9L        North York   
93        M9M        North York   
94        M9N              York   
95        M9P         Etobicoke   
96        M9R         Etobicoke   
97        M9V         Etobicoke   
98        M9W         Etobicoke   

                                        Neighborhoods  Accessories Store  \
0                                      Rouge, Malvern           0.000000   
1              Highland Creek, Rouge Hill, Port Union           0.000000   
2                   Guildwood, Morningside, West Hill           0.000000   
3                                              Woburn           0.000000   
4                                           Cedarbrae           0.000000   
5                                 Scarborough 

## Top 10 venues in each Postal Code

In [26]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
areaColumns = ['PostalCode', 'Borough', 'Neighborhoods']
freqColumns = []
for ind in np.arange(num_top_venues):
    try:
        freqColumns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        freqColumns.append('{}th Most Common Venue'.format(ind+1))
columns = areaColumns+freqColumns

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['PostalCode'] = toronto_grouped['PostalCode']
neighborhoods_venues_sorted['Borough'] = toronto_grouped['Borough']
neighborhoods_venues_sorted['Neighborhoods'] = toronto_grouped['Neighborhoods']

for ind in np.arange(toronto_grouped.shape[0]):
    row_categories = toronto_grouped.iloc[ind, :].iloc[3:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    neighborhoods_venues_sorted.iloc[ind, 3:] = row_categories_sorted.index.values[0:num_top_venues]

# neighborhoods_venues_sorted.sort_values(freqColumns, inplace=True)
print(neighborhoods_venues_sorted.shape)
neighborhoods_venues_sorted

(99, 13)


PostalCode           Borough  \
0         M1B       Scarborough   
1         M1C       Scarborough   
2         M1E       Scarborough   
3         M1G       Scarborough   
4         M1H       Scarborough   
5         M1J       Scarborough   
6         M1K       Scarborough   
7         M1L       Scarborough   
8         M1M       Scarborough   
9         M1N       Scarborough   
10        M1P       Scarborough   
11        M1R       Scarborough   
12        M1S       Scarborough   
13        M1T       Scarborough   
14        M1V       Scarborough   
15        M1W       Scarborough   
16        M2H        North York   
17        M2J        North York   
18        M2K        North York   
19        M2N        North York   
20        M2P        North York   
21        M2R        North York   
22        M3A        North York   
23        M3B        North York   
24        M3C        North York   
25        M3H        North York   
26        M3J        North York   
27        M3K        North York   
28        M3L        North York   
29        M3M        North York   
30        M3N        North York   
31        M4A        North York   
32        M4B         East York   
33        M4C         East York   
34        M4E      East Toronto   
35        M4G         East York   
36        M4H         East York   
37        M4J         East York   
38        M4K      East Toronto   
39        M4L      East Toronto   
40        M4M      East Toronto   
41        M4N   Central Toronto   
42        M4P   Central Toronto   
43        M4R   Central Toronto   
44        M4S   Central Toronto   
45        M4T   Central Toronto   
46        M4V   Central Toronto   
47        M4W  Downtown Toronto   
48        M4X  Downtown Toronto   
49        M4Y  Downtown Toronto   
50        M5A  Downtown Toronto   
51        M5B  Downtown Toronto   
52        M5C  Downtown Toronto   
53        M5E  Downtown Toronto   
54        M5G  Downtown Toronto   
55        M5H  Downtown Toronto   
56        M5J  Downtown Toronto   
57        M5K  Downtown Toronto   
58        M5L  Downtown Toronto   
59        M5M        North York   
60        M5N   Central Toronto   
61        M5P   Central Toronto   
62        M5R   Central Toronto   
63        M5S  Downtown Toronto   
64        M5T  Downtown Toronto   
65        M5V  Downtown Toronto   
66        M5W  Downtown Toronto   
67        M5X  Downtown Toronto   
68        M6A        North York   
69        M6B        North York   
70        M6C              York   
71        M6E              York   
72        M6G  Downtown Toronto   
73        M6H      West Toronto   
74        M6J      West Toronto   
75        M6K      West Toronto   
76        M6L        North York   
77        M6M              York   
78        M6N              York   
79        M6P      West Toronto   
80        M6R      West Toronto   
81        M6S      West Toronto   
82        M7A  Downtown Toronto   
83        M7R       Mississauga   
84        M7Y      East Toronto   
85        M8V         Etobicoke   
86        M8W         Etobicoke   
87        M8X         Etobicoke   
88        M8Y         Etobicoke   
89        M8Z         Etobicoke   
90        M9B         Etobicoke   
91        M9C         Etobicoke   
92        M9L        North York   
93        M9M        North York   
94        M9N              York   
95        M9P         Etobicoke   
96        M9R         Etobicoke   
97        M9V         Etobicoke   
98        M9W         Etobicoke   

                                        Neighborhoods  \
0                                      Rouge, Malvern   
1              Highland Creek, Rouge Hill, Port Union   
2                   Guildwood, Morningside, West Hill   
3                                              Woburn   
4                                           Cedarbrae   
5                                 Scarborough Village   
6         East Birchmount Park, Ionview, Kennedy Park   
7                     Clairlea, Golden Mile, O

# Clustering model

In [44]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop(["PostalCode", "Borough", "Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_
toronto_grouped

PostalCode           Borough  \
0         M1B       Scarborough   
1         M1C       Scarborough   
2         M1E       Scarborough   
3         M1G       Scarborough   
4         M1H       Scarborough   
5         M1J       Scarborough   
6         M1K       Scarborough   
7         M1L       Scarborough   
8         M1M       Scarborough   
9         M1N       Scarborough   
10        M1P       Scarborough   
11        M1R       Scarborough   
12        M1S       Scarborough   
13        M1T       Scarborough   
14        M1V       Scarborough   
15        M1W       Scarborough   
16        M2H        North York   
17        M2J        North York   
18        M2K        North York   
19        M2N        North York   
20        M2P        North York   
21        M2R        North York   
22        M3A        North York   
23        M3B        North York   
24        M3C        North York   
25        M3H        North York   
26        M3J        North York   
27        M3K        North York   
28        M3L        North York   
29        M3M        North York   
30        M3N        North York   
31        M4A        North York   
32        M4B         East York   
33        M4C         East York   
34        M4E      East Toronto   
35        M4G         East York   
36        M4H         East York   
37        M4J         East York   
38        M4K      East Toronto   
39        M4L      East Toronto   
40        M4M      East Toronto   
41        M4N   Central Toronto   
42        M4P   Central Toronto   
43        M4R   Central Toronto   
44        M4S   Central Toronto   
45        M4T   Central Toronto   
46        M4V   Central Toronto   
47        M4W  Downtown Toronto   
48        M4X  Downtown Toronto   
49        M4Y  Downtown Toronto   
50        M5A  Downtown Toronto   
51        M5B  Downtown Toronto   
52        M5C  Downtown Toronto   
53        M5E  Downtown Toronto   
54        M5G  Downtown Toronto   
55        M5H  Downtown Toronto   
56        M5J  Downtown Toronto   
57        M5K  Downtown Toronto   
58        M5L  Downtown Toronto   
59        M5M        North York   
60        M5N   Central Toronto   
61        M5P   Central Toronto   
62        M5R   Central Toronto   
63        M5S  Downtown Toronto   
64        M5T  Downtown Toronto   
65        M5V  Downtown Toronto   
66        M5W  Downtown Toronto   
67        M5X  Downtown Toronto   
68        M6A        North York   
69        M6B        North York   
70        M6C              York   
71        M6E              York   
72        M6G  Downtown Toronto   
73        M6H      West Toronto   
74        M6J      West Toronto   
75        M6K      West Toronto   
76        M6L        North York   
77        M6M              York   
78        M6N              York   
79        M6P      West Toronto   
80        M6R      West Toronto   
81        M6S      West Toronto   
82        M7A  Downtown Toronto   
83        M7R       Mississauga   
84        M7Y      East Toronto   
85        M8V         Etobicoke   
86        M8W         Etobicoke   
87        M8X         Etobicoke   
88        M8Y         Etobicoke   
89        M8Z         Etobicoke   
90        M9B         Etobicoke   
91        M9C         Etobicoke   
92        M9L        North York   
93        M9M        North York   
94        M9N              York   
95        M9P         Etobicoke   
96        M9R         Etobicoke   
97        M9V         Etobicoke   
98        M9W         Etobicoke   

                                        Neighborhoods  Accessories Store  \
0                                      Rouge, Malvern           0.000000   
1              Highland Creek, Rouge Hill, Port Union           0.000000   
2                   Guildwood, Morningside, West Hill           0.000000   
3                                              Woburn           0.000000   
4                                           Cedarbrae           0.000000   
5                                 Scarborough 

## New DataFrame with clustering data

In [37]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
toronto_merged = toronto_grouped.copy()
toronto_merged.shape

(99, 274)

In [38]:
# add clustering labels
toronto_merged["Cluster Labels"] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.drop(["Borough", "Neighborhoods"], 1).set_index("PostalCode"), on="PostalCode")

print(toronto_merged.shape)
toronto_merged.head() # check the last columns!

(99, 285)


PostalCode      Borough                           Neighborhoods  \
0        M1B  Scarborough                          Rouge, Malvern   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union   
2        M1E  Scarborough       Guildwood, Morningside, West Hill   
3        M1G  Scarborough                                  Woburn   
4        M1H  Scarborough                               Cedarbrae   

   Accessories Store  Airport  Airport Food Court  Airport Gate  \
0                0.0      0.0                 0.0           0.0   
1                0.0      0.0                 0.0           0.0   
2                0.0      0.0                 0.0           0.0   
3                0.0      0.0                 0.0           0.0   
4                0.0      0.0                 0.0           0.0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0             0.0              0.0               0.0                  0.0   
1             0.0              0.0               0.0                  0.0   
2             0.0              0.0               0.0                  0.0   
3             0.0              0.0               0.0                  0.0   
4             0.0              0.0               0.0                  0.0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0           0.0       0.0          0.0                  0.0               0.0   
1           0.0       0.0          0.0                  0.0               0.0   
2           0.0       0.0          0.0                  0.0               0.0   
3           0.0       0.0          0.0                  0.0               0.0   
4           0.0       0.0          0.0                  0.0               0.0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0            0.000000          0.0            0.0        0.0         0.0   
1            0.000000          0.0            0.0        0.0         0.0   
2            0.000000          0.0            0.0        0.0         0.0   
3            0.000000          0.0            0.0        0.0         0.0   
4            0.111111          0.0            0.0        0.0         0.0   

   Bagel Shop    Bakery      Bank  Bar  Baseball Field  Baseball Stadium  \
0         0.0  0.000000  0.000000  0.0             0.0               0.0   
1         0.0  0.000000  0.000000  0.5             0.0               0.0   
2         0.0  0.000000  0.000000  0.0             0.0               0.0   
3         0.0  0.000000  0.000000  0.0             0.0               0.0   
4         0.0  0.111111  0.111111  0.0             0.0               0.0   

   Basketball Court  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0               0.0                 0.0    0.0              0.0       0.0   
1               0.0                 0.0    0.0              0.0       0.0   
2               0.0                 0.0    0.0              0.0       0.0   
3               0.0                 0.0    0.0              0.0       0.0   
4               0.0                 0.0    0.0              0.0       0.0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Board Shop  \
0         0.0                 0.0        0.0     0.0         0.0   
1         0.0                 0.0        0.0     0.0         0.0   
2         0.0                 0.0        0.0     0.0         0.0   
3         0.0                 0.0        0.0     0.0         0.0   
4         0.0                 0.0        0.0     0.0         0.0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0            0.0        0.0       0.0                   0.0           0.000   
1            0.0        0.0       0.0                   0.0           0.000   
2            0.0        0.0       0.0                   0.0           0.125   
3            0.0        0.0       0.0                   0.0           0.000   
4            0.0        0.0       0.0                

In [39]:
# sort the results by Cluster Labels
print(toronto_merged.shape)
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged

(99, 285)


PostalCode           Borough  \
49        M4Y  Downtown Toronto   
67        M5X  Downtown Toronto   
66        M5W  Downtown Toronto   
65        M5V  Downtown Toronto   
64        M5T  Downtown Toronto   
63        M5S  Downtown Toronto   
62        M5R   Central Toronto   
61        M5P   Central Toronto   
60        M5N   Central Toronto   
59        M5M        North York   
58        M5L  Downtown Toronto   
57        M5K  Downtown Toronto   
56        M5J  Downtown Toronto   
55        M5H  Downtown Toronto   
54        M5G  Downtown Toronto   
53        M5E  Downtown Toronto   
52        M5C  Downtown Toronto   
51        M5B  Downtown Toronto   
50        M5A  Downtown Toronto   
97        M9V         Etobicoke   
68        M6A        North York   
69        M6B        North York   
70        M6C              York   
72        M6G  Downtown Toronto   
96        M9R         Etobicoke   
95        M9P         Etobicoke   
92        M9L        North York   
91        M9C         Etobicoke   
89        M8Z         Etobicoke   
88        M8Y         Etobicoke   
86        M8W         Etobicoke   
85        M8V         Etobicoke   
84        M7Y      East Toronto   
48        M4X  Downtown Toronto   
83        M7R       Mississauga   
81        M6S      West Toronto   
80        M6R      West Toronto   
79        M6P      West Toronto   
78        M6N              York   
77        M6M              York   
76        M6L        North York   
75        M6K      West Toronto   
74        M6J      West Toronto   
73        M6H      West Toronto   
82        M7A  Downtown Toronto   
46        M4V   Central Toronto   
98        M9W         Etobicoke   
21        M2R        North York   
23        M3B        North York   
3         M1G       Scarborough   
4         M1H       Scarborough   
5         M1J       Scarborough   
19        M2N        North York   
18        M2K        North York   
17        M2J        North York   
24        M3C        North York   
16        M2H        North York   
14        M1V       Scarborough   
13        M1T       Scarborough   
12        M1S       Scarborough   
11        M1R       Scarborough   
10        M1P       Scarborough   
9         M1N       Scarborough   
8         M1M       Scarborough   
15        M1W       Scarborough   
7         M1L       Scarborough   
25        M3H        North York   
2         M1E       Scarborough   
44        M4S   Central Toronto   
43        M4R   Central Toronto   
42        M4P   Central Toronto   
41        M4N   Central Toronto   
40        M4M      East Toronto   
39        M4L      East Toronto   
38        M4K      East Toronto   
1         M1C       Scarborough   
26        M3J        North York   
36        M4H         East York   
34        M4E      East Toronto   
33        M4C         East York   
32        M4B         East York   
31        M4A        North York   
30        M3N        North York   
29        M3M        North York   
28        M3L        North York   
35        M4G         East York   
6         M1K       Scarborough   
90        M9B         Etobicoke   
0         M1B       Scarborough   
93        M9M        North York   
20        M2P        North York   
45        M4T   Central Toronto   
71        M6E              York   
22        M3A        North York   
94        M9N              York   
27        M3K        North York   
37        M4J         East York   
87        M8X         Etobicoke   
47        M4W  Downtown Toronto   

                                        Neighborhoods  Accessories Store  \
49                               Church and Wellesley           0.000000   
67             First Canadian Place, Underground city           0.000000   
66                    Stn A PO Boxes 25 The Esplanade           0.000000   
65  CN Tower, Bathurst Quay, Island airport, Harbo...           0.000000   
64          Chinatown, Grange Park, Kensington Market           0.000000   
63                     Harbord, University of 

In [40]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, post, bor, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['PostalCode'], toronto_merged['Borough'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup('{} ({}): {} - Cluster {}'.format(bor, post, poi, cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

KeyError: 'Latitude'